In [43]:
# Google Colab Users change to True 
google_colab = False

if google_colab == True:
    import os
    import warnings
    warnings.simplefilter("ignore", DeprecationWarning)

    # Define a flag file path
    flag_file = "/content/setup_done"

    # Check if the setup has already been done
    if not os.path.exists(flag_file):
        print("Running setup for the first time...")

        # Clone the repository
        !git clone https://github.com/PriyeshGosai/ZA_Flex.git
        %cd ZA_Flex

        # Install PyPSA v0.32.0
        !pip install pypsa #==0.32.0

        # Create a flag file to indicate setup is done
        with open(flag_file, "w") as f:
            f.write("Setup complete")

    else:
        print("Setup already completed. Skipping installation.")


In [44]:
import os
import pandas as pd
import logging
import pypsa
import numpy as np
import plotly.express as px
import shutil
pd.options.plotting.backend = "plotly"
import warnings
import plotly.graph_objects as go
from plotly.subplots import make_subplots

warnings.filterwarnings(action='ignore', message='Data Validation extension is not supported and will be removed')
pd.options.mode.chained_assignment = None  # Suppress the warning

In [45]:
def convert_selected_sheets_to_csv(excel_file_path, csv_folder_path):
    """
    Reads an Excel file, checks if any sheets match a predefined list, and converts them into CSV files.

    Parameters:
    excel_file_path (str): The file path of the Excel file.
    csv_folder_path (str): The directory where CSV files should be saved.

    Returns:
    list: List of paths to the created CSV files.
    """
    logging.basicConfig(level=logging.INFO)

    if os.path.exists(csv_folder_path):
        shutil.rmtree(csv_folder_path)

    # Recreate the folder
    os.makedirs(csv_folder_path)

    created_csv_files = []

    # Initialize network
    n = pypsa.Network()

    # Extract relevant component names
    # all_variables = []
    # for key in n.component_attrs:
    #     attrs = n.component_attrs[key]  # Get the attribute DataFrame

    #     # Check if 'static' or 'varying' exists in columns
    #     has_static = "static" in attrs.columns
    #     has_varying = "varying" in attrs.columns

    #     for var in attrs.index:
    #         # Apply conditions: If 'static' or 'varying' exists, check their values
    #         if (has_static and attrs.loc[var, "static"]) or (has_varying and attrs.loc[var, "varying"]):
    #             list_name = n.components[key].get("list_name", key)  # Ensure safe access
    #             all_variables.append(f"{list_name}-{var}")

    # # Also include component list names and snapshots
    # all_variables.extend([n.components[key].get("list_name", key) for key in n.components])
    # all_variables.append('snapshots')

    all_variables = [
            *(f"networks-{suffix}" for suffix in [
                "name", "snapshots", "snapshot_weightings", "investment_periods",
                "investment_period_weightings", "now", "srid", "crs", "buses",
                "buses_t", "lines", "lines_t", "components", "components_t",
                "branches()", "graph()"
            ]),
            *(f"sub_networks-{suffix}" for suffix in ["name", "carrier", "slack_bus"]),
            *(f"buses-{suffix}" for suffix in [
                "name", "v_nom", "type", "x", "y", "carrier", "unit", "v_mag_pu_set",
                "v_mag_pu_min", "v_mag_pu_max", "control", "generator", "sub_network",
                "p", "q", "v_mag_pu", "v_ang", "marginal_price"
            ]),
            *(f"carriers-{suffix}" for suffix in ["name", "co2_emissions", "color", "nice_name", "max_growth", "max_relative_growth"]),
            *(f"global_constraints-{suffix}" for suffix in ["name", "type", "investment_period", "carrier_attribute", "sense", "constant", "mu"]),
            *(f"lines-{suffix}" for suffix in [
                "name", "bus0", "bus1", "type", "x", "r", "g", "b", "s_nom", "s_nom_mod",
                "s_nom_extendable", "s_nom_min", "s_nom_max", "s_max_pu", "capital_cost",
                "active", "build_year", "lifetime", "length", "carrier", "terrain_factor",
                "num_parallel", "v_ang_min", "v_ang_max", "sub_network", "p0", "q0",
                "p1", "q1", "x_pu", "r_pu", "g_pu", "b_pu", "x_pu_eff", "r_pu_eff",
                "s_nom_opt", "mu_lower", "mu_upper"
            ]),
            *(f"line_types-{suffix}" for suffix in [
                "name", "f_nom", "r_per_length", "x_per_length", "c_per_length",
                "i_nom", "mounting", "cross_section", "references"
            ]),
            *(f"transformers-{suffix}" for suffix in [
                "name", "bus0", "bus1", "type", "model", "x", "r", "g", "b", "s_nom",
                "s_nom_mod", "s_nom_extendable", "s_nom_min", "s_nom_max", "s_max_pu",
                "capital_cost", "num_parallel", "tap_ratio", "tap_side", "tap_position",
                "phase_shift", "active", "build_year", "lifetime", "v_ang_min",
                "v_ang_max", "sub_network", "p0", "q0", "p1", "q1", "x_pu", "r_pu",
                "g_pu", "b_pu", "x_pu_eff", "r_pu_eff", "s_nom_opt", "mu_lower",
                "mu_upper"
            ]),
            *(f"transformer_types-{suffix}" for suffix in [
                "name", "f_nom", "s_nom", "v_nom_0", "v_nom_1", "vsc", "vscr", "pfe",
                "i0", "phase_shift", "tap_side", "tap_neutral", "tap_min", "tap_max",
                "tap_step", "references"
            ]),
            *(f"links-{suffix}" for suffix in [
                "name", "bus0", "bus1", "type", "carrier", "efficiency", "active",
                "build_year", "lifetime", "p_nom", "p_nom_mod", "p_nom_extendable",
                "p_nom_min", "p_nom_max", "p_set", "p_min_pu", "p_max_pu",
                "capital_cost", "marginal_cost", "marginal_cost_quadratic",
                "stand_by_cost", "length", "terrain_factor", "committable",
                "start_up_cost", "shut_down_cost", "min_up_time", "min_down_time",
                "up_time_before", "down_time_before", "ramp_limit_up", "ramp_limit_down",
                "ramp_limit_start_up", "ramp_limit_shut_down", "p0", "p1",
                "p_nom_opt", "status", "mu_lower", "mu_upper", "mu_p_set",
                "mu_ramp_limit_up", "mu_ramp_limit_down"
            ]),
            *(f"loads-{suffix}" for suffix in ["name", "bus", "carrier", "type", "p_set", "q_set", "sign", "p", "q", "active"]),
            *(f"generators-{suffix}" for suffix in [
                "name", "bus", "control", "type", "p_nom", "p_nom_mod",
                "p_nom_extendable", "p_nom_min", "p_nom_max", "p_min_pu", "p_max_pu",
                "p_set", "e_sum_min", "e_sum_max", "q_set", "sign", "carrier",
                "marginal_cost", "marginal_cost_quadratic", "active", "build_year",
                "lifetime", "capital_cost", "efficiency", "committable", "start_up_cost",
                "shut_down_cost", "stand_by_cost", "min_up_time", "min_down_time",
                "up_time_before", "down_time_before", "ramp_limit_up", "ramp_limit_down",
                "ramp_limit_start_up", "ramp_limit_shut_down", "weight", "p", "q",
                "p_nom_opt", "status", "mu_upper", "mu_lower", "mu_p_set",
                "mu_ramp_limit_up", "mu_ramp_limit_down"
            ]),
            *(f"storage_units-{suffix}" for suffix in [
                "name", "bus", "control", "type", "p_nom", "p_nom_mod",
                "p_nom_extendable", "p_nom_min", "p_nom_max", "p_min_pu", "p_max_pu",
                "p_set", "q_set", "sign", "carrier", "spill_cost", "marginal_cost",
                "marginal_cost_quadratic", "marginal_cost_storage", "capital_cost",
                "active", "build_year", "lifetime", "state_of_charge_initial",
                "state_of_charge_initial_per_period", "state_of_charge_set",
                "cyclic_state_of_charge", "cyclic_state_of_charge_per_period",
                "max_hours", "efficiency_store", "efficiency_dispatch",
                "standing_loss", "inflow", "p", "p_dispatch", "p_store", "q",
                "state_of_charge", "spill", "p_nom_opt", "mu_upper", "mu_lower",
                "mu_state_of_charge_set", "mu_energy_balance"
            ]),
            *(f"stores-{suffix}" for suffix in [
                "name", "bus", "type", "carrier", "e_nom", "e_nom_mod", "e_nom_extendable",
                "e_nom_min", "e_nom_max", "e_min_pu", "e_max_pu", "e_initial",
                "e_initial_per_period", "e_cyclic", "e_cyclic_per_period", "p_set",
                "q_set", "sign", "marginal_cost", "marginal_cost_quadratic",
                "marginal_cost_storage", "capital_cost", "standing_loss", "active",
                "build_year", "lifetime", "p", "q", "e", "e_nom_opt", "mu_upper",
                "mu_lower", "mu_energy_balance"
            ]),
            "networks", "sub_networks", "buses", "carriers", "global_constraints",
            "lines", "line_types", "transformers", "transformer_types", "links",
            "loads", "generators", "storage_units", "stores", "shunt_impedances",
            "shapes", "snapshots"
        ]

    xls = None  # Initialize xls variable

    try:
        # Load Excel file
        xls = pd.ExcelFile(excel_file_path)

        # Iterate through sheets in the predefined list
        for sheet_name in xls.sheet_names:
            if sheet_name in all_variables:
                # Read sheet into DataFrame
                df = xls.parse(sheet_name)

                # Define the output CSV file path
                csv_file_path = os.path.join(csv_folder_path, f"{sheet_name}.csv")

                # Save DataFrame as CSV
                df.to_csv(csv_file_path, index=False)

                logging.info(f"Converted {sheet_name} to CSV.")
                created_csv_files.append(csv_file_path)

        logging.info(f"Conversion complete. CSV files are saved in '{csv_folder_path}'")
        return csv_folder_path

    except Exception as e:
        logging.error(f"Error processing Excel file: {e}")
        return []

    finally:
        # Explicitly close the Excel file
        if xls is not None:
            xls.close()
            logging.info("Excel file closed successfully.")


In [46]:
input_file = 'South_Africa_V0.xlsx'
path = convert_selected_sheets_to_csv(input_file, 'model_folder')

INFO:root:Converted buses to CSV.
INFO:root:Converted generators to CSV.
INFO:root:Converted storage_units to CSV.
INFO:root:Converted carriers to CSV.
INFO:root:Converted loads to CSV.
INFO:root:Converted loads-p_set to CSV.
INFO:root:Converted snapshots to CSV.
INFO:root:Converted generators-p_max_pu to CSV.
INFO:root:Conversion complete. CSV files are saved in 'model_folder'
INFO:root:Excel file closed successfully.


In [47]:
network = pypsa.Network()

network.import_from_csv_folder(path)


INFO:pypsa.io:Imported network model_folder has buses, carriers, generators, loads, storage_units


In [48]:
# Define the new time range
start_time = "2019-01-01 00:00:00"  # Replace with your desired start timestamp
end_time = "2019-02-08 23:00:00"    # Replace with your desired end timestamp

# Ensure timestamps are in datetime format
network.snapshots = network.snapshots[(network.snapshots >= pd.Timestamp(start_time)) & 
                                      (network.snapshots <= pd.Timestamp(end_time))]

In [49]:
network.generators

bus control type  p_nom  p_nom_mod  \
Generator                                                        
Arnot 1            South Africa      PQ       392.0        0.0   
Arnot 2            South Africa      PQ       392.0        0.0   
Arnot 3            South Africa      PQ       392.0        0.0   
Arnot 4            South Africa      PQ       392.0        0.0   
Arnot 5            South Africa      PQ       392.0        0.0   
...                         ...     ...  ...    ...        ...   
Kathu Solar        South Africa      PQ       100.0        0.0   
Bokpoort CSP       South Africa      PQ        50.0        0.0   
Ngodwana Biomass   South Africa      PQ        25.0        0.0   
Loadshedding       South Africa      PQ         1.0        0.0   
Sync Condenser     South Africa      PQ         1.0        0.0   

                   p_nom_extendable  p_nom_min  p_nom_max  p_min_pu  p_max_pu  \
Generator                                                                       
Arnot 1                       False        0.0        inf       0.4       1.0   
Arnot 2                       False        0.0        inf       0.4       1.0   
Arnot 3                       False        0.0        inf       0.4       1.0   
Arnot 4                       False        0.0        inf       0.4       1.0   
Arnot 5                       False        0.0        inf       0.4       1.0   
...                             ...        ...        ...       ...       ...   
Kathu Solar                   False        0.0        inf       0.0       1.0   
Bokpoort CSP                  False        0.0        inf       0.0       1.0   
Ngodwana Biomass              False        0.0        inf       0.1       1.0   
Loadshedding                   True        0.0        inf       0.0       1.0   
Sync Condenser                 True        0.0        inf      -1.0       0.0   

                   ...  up_time_before  down_time_before  ramp_limit_up  \
Generator          ...                                                    
Arnot 1            ...               1                 0            2.0   
Arnot 2            ...               1                 0            2.0   
Arnot 3            ...               1                 0            2.0   
Arnot 4            ...               1                 0            2.0   
Arnot 5            ...               1                 0            2.0   
...                ...             ...               ...            ...   
Kathu Solar        ...               1                 0            NaN   
Bokpoort CSP       ...               1                 0            NaN   
Ngodwana Biomass   ...               1                 0            1.0   
Loadshedding       ...               1                 0            NaN   
Sync Condenser     ...               1                 0            NaN   

                   ramp_limit_down  ramp_limit_start_up ramp_limit_shut_down  \
Generator                                                                      
Arnot 1                        2.0                  1.0                  1.0   
Arnot 2                        2.0                  1.0                  1.0   
Arnot 3                        2.0                  1.0                  1.0   
Arnot 4                        2.0                  1.0                  1.0   
Arnot 5                        2.0                  1.0                  1.0   
...                            ...                  ...                  ...   
Kathu Solar                    NaN                  1.0                  1.0   
Bokpoort CSP                   NaN                  1.0                  1.0   
Ngodwana Biomass               1.0                  1.0                  1.0   
Loadshedding                   NaN                  1.0                  1.0   
Sync Condenser                 NaN                  1.0                  1.0   

                   weight  p_nom_opt        y        x  
Generator                                

In [50]:
network.generators_t.p_max_pu

Generator            Kathu Solar   Jeffreys Bay Wind   Kalkbult Solar   \
snapshot                                                                 
2019-01-01 00:00:00           0.0            0.457870              0.0   
2019-01-01 01:00:00           0.0            0.481697              0.0   
2019-01-01 02:00:00           0.0            0.506153              0.0   
2019-01-01 03:00:00           0.0            0.511330              0.0   
2019-01-01 04:00:00           0.0            0.598936              0.0   
...                           ...                 ...              ...   
2019-02-08 19:00:00           0.0            1.592849              0.0   
2019-02-08 20:00:00           0.0            1.602671              0.0   
2019-02-08 21:00:00           0.0            1.591293              0.0   
2019-02-08 22:00:00           0.0            1.574450              0.0   
2019-02-08 23:00:00           0.0            1.533858              0.0   

Generator            Cookhouse Wind   Jasper Solar   Gouda Wind Farm   \
snapshot                                                                
2019-01-01 00:00:00           0.4723            0.0          0.625087   
2019-01-01 01:00:00           0.5085            0.0          0.675974   
2019-01-01 02:00:00           0.5147            0.0          0.572476   
2019-01-01 03:00:00           0.5425            0.0          0.554932   
2019-01-01 04:00:00           0.5819            0.0          0.539278   
...                              ...            ...               ...   
2019-02-08 19:00:00           0.7565            0.0          0.778459   
2019-02-08 20:00:00           0.7810            0.0          0.761037   
2019-02-08 21:00:00           0.7956            0.0          0.705410   
2019-02-08 22:00:00           0.7765            0.0          0.642165   
2019-02-08 23:00:00           0.7719            0.0          0.616910   

Generator            Bokpoort CSP   
snapshot                            
2019-01-01 00:00:00            0.0  
2019-01-01 01:00:00            0.0  
2019-01-01 02:00:00            0.0  
2019-01-01 03:00:00            0.0  
2019-01-01 04:00:00            0.0  
...                            ...  
2019-02-08 19:00:00            0.0  
2019-02-08 20:00:00            0.0  
2019-02-08 21:00:00            0.0  
2019-02-08 22:00:00            0.0  
2019-02-08 23:00:00            0.0  

[936 rows x 7 columns]

In [51]:
network.links

Empty DataFrame
Columns: [bus0, bus1, type, carrier, efficiency, active, build_year, lifetime, p_nom, p_nom_mod, p_nom_extendable, p_nom_min, p_nom_max, p_set, p_min_pu, p_max_pu, capital_cost, marginal_cost, marginal_cost_quadratic, stand_by_cost, length, terrain_factor, committable, start_up_cost, shut_down_cost, min_up_time, min_down_time, up_time_before, down_time_before, ramp_limit_up, ramp_limit_down, ramp_limit_start_up, ramp_limit_shut_down, p_nom_opt]
Index: []

[0 rows x 34 columns]

In [52]:
network.optimize(solver='highs')

INFO:linopy.model: Solve problem using Highs solver
INFO:linopy.model:Solver options:
 - solver: highs
INFO:linopy.io:Writing objective.
Writing continuous variables.: 100%|██████████| 6/6 [00:00<00:00, 22.63it/s]
INFO:linopy.io: Writing time: 2.55s
INFO:linopy.constants: Optimization successful: 
Status: ok
Termination condition: optimal
Solution: 106706 primals, 402280 duals
Objective: 1.30e+10
Solver model: available
Solver message: optimal

INFO:pypsa.optimization.optimize:The shadow-prices of the constraints Generator-fix-p-lower, Generator-fix-p-upper, Generator-ext-p-lower, Generator-ext-p-upper, Generator-fix-p-ramp_limit_up, Generator-fix-p-ramp_limit_down, StorageUnit-fix-p_dispatch-lower, StorageUnit-fix-p_dispatch-upper, StorageUnit-fix-p_store-lower, StorageUnit-fix-p_store-upper, StorageUnit-fix-state_of_charge-lower, StorageUnit-fix-state_of_charge-upper, StorageUnit-energy_balance were not assigned to the network.


('ok', 'optimal')

In [53]:
network.generators_t.p.plot()

c:\Users\gosai\anaconda3\envs\pypsa-eur\Lib\site-packages\_plotly_utils\basevalidators.py:2596: DeprecationWarning:

*scattermapbox* is deprecated! Use *scattermap* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



In [ ]:
# Check the minimum generators per unit. 
network.generators_t.p.min().plot(kind = 'bar')

c:\Users\gosai\anaconda3\envs\pypsa-eur\Lib\site-packages\_plotly_utils\basevalidators.py:2596: DeprecationWarning:

*scattermapbox* is deprecated! Use *scattermap* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



In [54]:
network.storage_units_t.p.plot()

c:\Users\gosai\anaconda3\envs\pypsa-eur\Lib\site-packages\_plotly_utils\basevalidators.py:2596: DeprecationWarning:

*scattermapbox* is deprecated! Use *scattermap* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



In [55]:
network.storage_units_t.state_of_charge.plot()

c:\Users\gosai\anaconda3\envs\pypsa-eur\Lib\site-packages\_plotly_utils\basevalidators.py:2596: DeprecationWarning:

*scattermapbox* is deprecated! Use *scattermap* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



In [56]:
network.storage_units_t.spill.plot()

c:\Users\gosai\anaconda3\envs\pypsa-eur\Lib\site-packages\_plotly_utils\basevalidators.py:2596: DeprecationWarning:

*scattermapbox* is deprecated! Use *scattermap* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/

